In [0]:
dbutils.fs.ls("/FileStore/tables")

Out[4]: [FileInfo(path='dbfs:/FileStore/tables/authentication_credentials.csv', name='authentication_credentials.csv', size=202, modificationTime=1687110999000)]

In [0]:
# pyspark functions
from pyspark.sql.functions import *
# URL processing
import urllib

In [0]:
# Specify file type to be csv
file_type = "csv"
# Indicates file has first row as the header
first_row_is_header = "true"
# Indicates file has comma as the delimeter
delimiter = ","
# Read the CSV file to spark dataframe
aws_keys_df = spark.read.format(file_type)\
.option("header", first_row_is_header)\
.option("sep", delimiter)\
.load("/FileStore/tables/authentication_credentials.csv")

In [0]:
# Get the AWS access key and secret key from the spark dataframe
ACCESS_KEY = aws_keys_df.where(col('User name')=='databricks-user').select('Access key ID').collect()[0]['Access key ID']
SECRET_KEY = aws_keys_df.where(col('User name')=='databricks-user').select('Secret access key').collect()[0]['Secret access key']
# Encode the secrete key
ENCODED_SECRET_KEY = urllib.parse.quote(string=SECRET_KEY, safe="")

In [0]:
# AWS S3 bucket name
AWS_S3_BUCKET = "user-0a48d8473ced-bucket"
# Mount name for the bucket
MOUNT_NAME = "/mnt/user-0a48d8473ced-bucket"
# Source url
SOURCE_URL = "s3n://{0}:{1}@{2}".format(ACCESS_KEY, ENCODED_SECRET_KEY, AWS_S3_BUCKET)
# Mount the drive
dbutils.fs.mount(SOURCE_URL, MOUNT_NAME)

Out[8]: True

In [0]:
display(dbutils.fs.ls("/mnt/user-0a48d8473ced-bucket/../.."))

path name size modificationTime dbfs:/FileStore/ FileStore/ 0 1697025807192 dbfs:/Volume/ Volume/ 0 0 dbfs:/Volumes/ Volumes/ 0 0 dbfs:/databricks-datasets/ databricks-datasets/ 0 0 dbfs:/databricks-results/ databricks-results/ 0 0 dbfs:/delta/ delta/ 0 1697025807192 dbfs:/df_pin.csv/ df_pin.csv/ 0 1697025807192 dbfs:/local_disk0/ local_disk0/ 0 1697025807192 dbfs:/mnt/ mnt/ 0 1697025807192 dbfs:/pin_kinesis_events/ pin_kinesis_events/ 0 1697025807192 dbfs:/tmp/ tmp/ 0 1697025807192 dbfs:/user/ user/ 0 1697025807192 dbfs:/volume/ volume/ 0 0 dbfs:/volumes/ volumes/ 0 0

In [0]:
# File location and type
# Asterisk(*) indicates reading all the content of the specified file that have .json extension
file_location_pin = "/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/*.json"
file_location_geo = "/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.geo/partition=0/*.json" 
file_location_user = "/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.user/partition=0/*.json" 

file_type = "json"
# Ask Spark to infer the schema
infer_schema = "true"
# Read in JSONs from mounted S3 bucket
df_pin = spark.read.format(file_type) \
.option("inferSchema", infer_schema) \
.load(file_location_pin)
df_geo = spark.read.format(file_type) \
.option("inferSchema", infer_schema) \
.load(file_location_geo)
df_user = spark.read.format(file_type) \
.option("inferSchema", infer_schema) \
.load(file_location_user)

# Display Spark dataframe to check its content
display(df_pin)
display(df_geo)
display(df_user)

category description downloaded follower_count image_src index is_image_or_video poster_name save_location tag_list title unique_id event-planning Το όνομα που επέλεξε η μαμά Ανδριανή για τη γλυκιά Τιτίκα δεν είναι καθόλου τυχαίο. Και φυσικά δεν άφησε τίποτα στην τύχη ούτε την ημέρα της βάπτισης. Ανέθεσε την οργάνωση στην…  1 4 https://i.pinimg.com/originals/db/aa/d2/dbaad28fa85012a4ea6958540d98a8e5.jpg 4387 image Manosbojana Katsareas Local save in /data/event-planning Diy Flowers,Flower Diy,Baptism Decorations,Christening,Event Planning,Wedding Planner,Baptism Ideas,Birthday,Party Βάπτιση: H παραμυθένια βάπτιση της Τιτίκας με θέμα το μονόκερο από την e.m. for you ae5e7377-f1bd-4ac5-94de-bee317f51a43 home-decor Традиционные шведские коттеджи, обычно с красным фасадом — это настоящее воплощением идеального зимнего уюта. Они обычно оформлены очень просто и ✌PUFIK. Beautiful Interiors. On…  1 136k https://i.pinimg.com/originals/32/eb/72/32eb72e4fd8654c115a64528bd1f34b4.png 6717 image PUFIK Interiors & Inspirations Local save in /data/home-decor Scandinavian Cottage,Swedish Cottage,Swedish Home Decor,Swedish Farmhouse,Swedish Style,Swedish Kitchen,Kitchen Black,Swedish House,Cozy Cottage 〚 Уютные шведские коттеджи от Carina Olander 〛 ◾ Фото ◾ Идеи ◾ Дизайн bc5ab9ee-505e-44f6-92ba-677fe4fdf3e3 event-planning 15.1k Likes, 83 Comments - THE EVENT COLLECTIVE ✖️ (@theeventcollectivex) on Instagram: “I’ve always loved emerald green 🌲 by @a.purnellproduction Beautiful balloons by…” 1 311 https://i.pinimg.com/originals/91/0b/5c/910b5c120f7d1570ffc840302d7b49f4.jpg 4858 image Marie Bradford Local save in /data/event-planning Diy Birthday Decorations,Balloon Decorations,Table Decorations,Emerald Green Decor,40th Birthday Parties,24th Birthday,Surprise Birthday,Brunch Decor,Quinceanera Themes THE EVENT COLLECTIVE ✖️ on Instagram: “I’ve always loved emerald green 🌲 by @a.purnellproduction Beautiful balloons by @basicallycuteevents @inspiredengravings for the acrylic…” 58101415-9273-4311-a5bd-0015a56579b4 event-planning Wow your guests! Our backdrops are a great option for providing a personalized, stylish and fun addition to your party .It will be the focal point in any event! They are great a…  1 1k https://i.pinimg.com/originals/15/1f/93/151f93d662dc158ca2c9bbfed198f556.jpg 4608 image Iconica Design | Personalized Event Decor, Stationery & Gifts Local save in /data/event-planning Christmas Party Backdrop,Holiday Banner,Birthday Backdrop,Circus First Birthday,First Birthday Banners,Dinasour Birthday,Birthday Bash,Banner Backdrop,Photo Booth Backdrop Virtual Baby Shower Little Man Baby Shower Banner, Mustache Baby Shower Backdrop, Oh Boy, Any Color, Printed Or Printable File BBS0035 - 10x8 ft / Top Pole Pocket d234e56f-5b18-4ef3-905b-44103f7719d9 home-decor 6,636 Likes, 141 Comments - The Cottage Journal (@thecottagejournal) on Instagram: “Can you say color?! 😍😍😍 We are loving the cheery vibes that these aqua blue cabinets are g…  1 394 https://i.pinimg.com/originals/8c/17/a2/8c17a257b70780480bb89c3699363144.jpg 6633 image Sarah Martin Local save in /data/home-decor Diy Kitchen Cabinets,Kitchen Redo,Home Decor Kitchen,New Kitchen,Home Kitchens,Kitchen Remodeling,Aqua Kitchen,Kitchen Counters,Kitchen Islands The Cottage Journal on Instagram: “Can you say color?! 😍😍😍 We are loving the cheery vibes that these aqua blue cabinets are giving. If you could paint your cabinets any…” d136f6bc-840d-44f8-bbad-115eb7e6c51e christmas Make your own gingerbread person with our free Christmas craft. 4 pages of accessories to mix & match! #gingerbreadchristmasdecor #gingerbreadcraftspreschool #gingerbreadcraftfo…  1 7k https://i.pinimg.com/originals/ca/59/b1/ca59b1055ca52521b9ebd01799513b8c.jpg 2539 image Mrs. Merry | Free Printables for Kids, Holiday Printables & Party Local save in /data/christmas Christmas Projects For Kids,Christmas To Do List,Christmas Decorations For Kids,Christmas Activities For Kids,Preschool Christmas,Free Christmas Printables,Chris

country ind latitude longitude timestamp British Indian Ocean Territory (Chagos Archipelago) 9455 -82.9272 -150.346 2022-03-15 01:46:32 British Indian Ocean Territory (Chagos Archipelago) 6814 -86.5675 -149.565 2022-09-02 11:34:28 British Indian Ocean Territory (Chagos Archipelago) 7151 -14.6744 -75.3714 2020-06-05 23:37:24 British Indian Ocean Territory (Chagos Archipelago) 8221 -20.5574 -54.4834 2021-12-29 06:33:46 British Indian Ocean Territory (Chagos Archipelago) 7569 -86.5675 -149.565 2018-10-16 08:40:26 British Indian Ocean Territory (Chagos Archipelago) 5111 -83.7472 8.65953 2021-04-01 00:56:57 British Indian Ocean Territory (Chagos Archipelago) 2989 -87.013 133.062 2020-01-09 19:18:54 British Indian Ocean Territory (Chagos Archipelago) 1624 9.50751 119.757 2020-10-24 11:13:47 Antarctica (the territory South of 60 deg S) 10073 -32.8885 -170.295 2021-06-29 19:56:04 Antarctica (the territory South of 60 deg S) 10073 -32.8885 -170.295 2021-06-29 19:56:04 Antarctica (the territory South of 60 deg S) 2418 -88.4642 -171.061 2022-05-27 11:30:59 Antarctica (the territory South of 60 deg S) 2418 -88.4642 -171.061 2022-05-27 11:30:59 Antarctica (the territory South of 60 deg S) 5162 -71.6607 -149.206 2019-09-27 19:06:43 Antarctica (the territory South of 60 deg S) 1335 -77.9931 -175.682 2022-03-19 17:29:42 Antarctica (the territory South of 60 deg S) 9185 -10.3764 -22.9809 2019-10-06 18:12:55 Antarctica (the territory South of 60 deg S) 9335 -88.4642 -171.061 2020-11-14 23:42:22 Antarctica (the territory South of 60 deg S) 6749 -88.4642 -171.061 2018-04-16 07:39:46 South Georgia and the South Sandwich Islands 10507 -89.4786 -68.913 2018-12-27 23:57:31 Antarctica (the territory South of 60 deg S) 1729 -88.4642 -171.061 2021-05-04 14:59:44 Antarctica (the territory South of 60 deg S) 8836 -75.0203 -108.272 2022-09-06 23:57:01 Antarctica (the territory South of 60 deg S) 4361 -24.8372 -163.337 2022-07-17 10:48:12 Antarctica (the territory South of 60 deg S) 9117 -88.4642 -171.061 2018-08-02 03:26:24 Antarctica (the territory South of 60 deg S) 8836 -75.0203 -108.272 2022-09-06 23:57:01 Antarctica (the territory South of 60 deg S) 5162 -71.6607 -149.206 2019-09-27 19:06:43 Antarctica (the territory South of 60 deg S) 5625 -84.9073 -105.769 2020-11-22 21:47:04 Antarctica (the territory South of 60 deg S) 1752 -88.4642 -171.061 2020-11-23 15:01:39 Antarctica (the territory South of 60 deg S) 1872 -68.2538 -171.706 2020-11-02 17:14:08 Antarctica (the territory South of 60 deg S) 8156 -88.4642 -171.061 2022-08-24 22:19:55 Antarctica (the territory South of 60 deg S) 1910 -88.4642 -171.061 2020-06-14 01:25:40 Antarctica (the territory South of 60 deg S) 9031 -88.4642 -171.061 2019-12-15 01:10:49 Antarctica (the territory South of 60 deg S) 5237 -84.9073 -105.769 2021-07-04 15:50:48 Antarctica (the territory South of 60 deg S) 2147 -88.4642 -171.061 2018-08-15 14:23:56 Antarctica (the territory South of 60 deg S) 9121 -77.9931 -175.682 2019-11-03 20:15:30 Antarctica (the territory South of 60 deg S) 2201 -57.9438 -148.044 2020-02-01 11:55:43 Antarctica (the territory South of 60 deg S) 5891 -68.2538 -171.706 2021-03-22 00:33:27 South Georgia and the South Sandwich Islands 4739 80.6966 -69.2346 2020-05-29 08:14:30 Antarctica (the territory South of 60 deg S) 8577 -72.136 -130.529 2018-05-23 01:53:25 South Georgia and the South Sandwich Islands 5766 -51.534 -82.5598 2020-03-17 09:59:36 Antarctica (the territory South of 60 deg S) 7090 -62.92 -63.7974 2022-01-08 18:53:52 Antarctica (the territory South of 60 deg S) 624 -41.1737 170.227 2019-07-01 14:55:07 Antarctica (the territory South of 60 deg S) 624 -41.1737 170.227 2019-07-01 14:55:07 Antarctica (the territory South of 60 deg S) 2456 -31.2898 110.65 2019-05-17 16:01:23 Antarctica (the territory South of 60 deg S) 4790 45.2499 11.5767 2021-05-24 08:49:25 Antarctica (the territory South of 60 deg S) 60 -31.2898 110.65 2022-05-27 11:06:08 United States Minor Outlying Islands 7069 -77.4399 

age date_joined first_name ind last_name 42 2017-02-18 00:31:22 Christopher 6353 Hernandez 27 2016-03-08 13:38:37 Christopher 2015 Bradshaw 59 2017-05-12 21:22:17 Alexander 10673 Cervantes 48 2016-02-27 16:57:44 Christopher 1857 Hamilton 45 2016-09-15 06:02:53 Christopher 10020 Hawkins 35 2015-10-22 22:42:23 Christopher 2041 Campbell 48 2016-06-13 17:09:14 Christopher 7031 Anderson 50 2017-02-07 08:09:03 Benjamin 8075 Fitzpatrick 36 2016-06-01 09:41:09 Christopher 2539 Williams 39 2016-06-29 20:43:59 Christina 6398 Davenport 20 2015-10-23 04:13:23 Alexandria 3599 Alvarado 20 2015-10-23 04:13:23 Alexandria 4256 Alvarado 44 2016-12-18 16:05:39 Michelle 1901 Richardson 20 2015-10-23 04:13:23 Alexandria 3831 Alvarado 23 2015-10-31 19:20:09 Alexandria 6602 Anderson 20 2015-10-23 04:13:23 Alexandria 4249 Alvarado 20 2015-10-23 04:13:23 Alexandria 4245 Alvarado 26 2016-06-16 14:07:36 Catherine 10677 Mitchell 20 2015-10-23 04:13:23 Alexandria 3896 Alvarado 55 2017-08-12 13:26:38 Alexander 2161 Rodriguez 30 2016-03-02 23:44:12 Christopher 813 Gonzalez 22 2016-03-24 09:38:54 Christopher 2595 Barnett 20 2015-10-23 04:13:23 Alexandria 3717 Alvarado 20 2015-10-23 04:13:23 Alexandria 3475 Alvarado 45 2016-09-15 06:02:53 Christopher 9582 Hawkins 23 2015-10-31 19:20:09 Alexandria 5930 Anderson 20 2015-10-23 04:13:23 Alexandria 4249 Alvarado 20 2015-10-23 04:13:23 Alexandria 3705 Alvarado 28 2016-10-26 19:31:58 Christopher 6156 Alvarez 20 2015-10-23 04:13:23 Alexandria 4245 Alvarado 20 2015-10-23 04:13:23 Alexandria 4089 Alvarado 20 2015-10-23 04:13:23 Alexandria 4000 Alvarado 20 2015-10-23 04:13:23 Alexandria 4222 Alvarado 23 2016-10-01 06:22:38 Elizabeth 1282 Mccormick 20 2015-10-23 04:13:23 Alexandria 4044 Alvarado 20 2015-10-23 04:13:23 Alexandria 4008 Alvarado 20 2015-10-23 04:13:23 Alexandria 3767 Alvarado 20 2015-10-23 04:13:23 Alexandria 4086 Alvarado 49 2016-05-23 19:42:19 Jennifer 10190 Blanchard 20 2015-10-23 04:13:23 Alexandria 4096 Alvarado 24 2016-04-06 20:17:29 Christopher 8221 Edwards 20 2015-10-23 04:13:23 Alexandria 4317 Alvarado 20 2015-10-23 04:13:23 Alexandria 3964 Alvarado 20 2015-10-23 04:13:23 Alexandria 3539 Alvarado 20 2015-10-23 04:13:23 Alexandria 4087 Alvarado 20 2015-10-23 04:13:23 Alexandria 3790 Alvarado 20 2015-12-01 15:08:31 Christopher 5076 Butler 39 2017-07-19 07:12:04 Michelle 7790 Gutierrez 49 2016-04-22 20:36:02 Brittany 10509 Thompson 25 2016-08-19 02:29:26 Elizabeth 10248 English 30 2016-09-05 12:31:44 Jonathan 1487 Rodriguez 31 2016-07-30 01:45:47 Valerie 10917 Rodriguez 28 2015-12-18 10:50:10 Jennifer 10734 Arellano 24 2016-01-12 17:59:43 Brandon 10429 Henderson 24 2016-06-26 00:05:17 Samantha 2946 Carpenter 49 2016-02-27 04:42:03 Robert 10600 Mclaughlin 30 2016-09-05 12:31:44 Jonathan 1487 Rodriguez 40 2017-03-07 21:33:30 Christopher 4761 Norman 53 2017-04-05 13:59:02 Garrett 10721 Hernandez 27 2016-03-03 11:25:21 Christina 7206 Anderson 25 2016-04-15 17:06:49 Christopher 6806 Daniel 27 2016-04-11 21:27:52 Andrea 2267 Blankenship 24 2016-03-24 23:39:08 Danielle 2532 Hernandez 39 2017-07-19 07:12:04 Michelle 7790 Gutierrez 42 2016-02-08 16:47:33 Christopher 10675 Combs 25 2016-02-14 23:08:47 Christopher 1969 Haynes 44 2016-12-10 09:13:47 Kathleen 10274 Hamilton 25 2016-11-01 23:16:19 Christopher 9774 Foster 36 2017-08-18 16:25:58 Jonathan 5379 Rodriguez 27 2016-04-11 21:27:52 Andrea 2004 Blankenship 31 2016-01-17 23:28:43 Charles 2456 Hutchinson 57 2016-05-02 05:30:16 Katherine 7739 Peterson 27 2016-03-03 11:25:21 Christina 7219 Anderson 35 2016-01-28 23:57:43 Christopher 4908 Greene 26 2017-05-14 21:09:12 Jennifer 10842 Gonzalez 20 2015-12-01 15:08:31 Christopher 4752 Butler 49 2016-02-27 04:42:03 Robert 10600 Mclaughlin 45 2016-01-03 14:51:10 Jennifer 8122 Robertson 27 2017-08-09 15:14:15 Cassandra 1404 Browning 49 2016-12-25 19:30:02 Kimberly 9684 Hernandez 56 2017-09-06 08:07:57 Christopher 1476 Romero 20 2015-11-24 21:01:23 Alejandra 10746 Acevedo 39 2017-09-13 11:21:05 Michelle 8301 Hernandez 40

In [0]:
display(dbutils.fs.ls("/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/"))


path name size modificationTime dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000000.json 0a48d8473ced.pin+0+0000000000.json 444 1696877757000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000001.json 0a48d8473ced.pin+0+0000000001.json 681 1696877760000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000002.json 0a48d8473ced.pin+0+0000000002.json 714 1696877763000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000003.json 0a48d8473ced.pin+0+0000000003.json 640 1696877766000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000004.json 0a48d8473ced.pin+0+0000000004.json 444 1696877800000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000005.json 0a48d8473ced.pin+0+0000000005.json 681 1696877803000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000006.json 0a48d8473ced.pin+0+0000000006.json 444 1697024999000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000007.json 0a48d8473ced.pin+0+0000000007.json 681 1697025002000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000008.json 0a48d8473ced.pin+0+0000000008.json 714 1697025004000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000009.json 0a48d8473ced.pin+0+0000000009.json 640 1697025007000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000010.json 0a48d8473ced.pin+0+0000000010.json 643 1697025009000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000011.json 0a48d8473ced.pin+0+0000000011.json 602 1697025011000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000012.json 0a48d8473ced.pin+0+0000000012.json 767 1697025013000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000013.json 0a48d8473ced.pin+0+0000000013.json 509 1697025015000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000014.json 0a48d8473ced.pin+0+0000000014.json 810 1697025017000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000015.json 0a48d8473ced.pin+0+0000000015.json 766 1697025019000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000016.json 0a48d8473ced.pin+0+0000000016.json 680 1697025020000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000017.json 0a48d8473ced.pin+0+0000000017.json 448 1697025022000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000018.json 0a48d8473ced.pin+0+0000000018.json 760 1697025025000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000019.json 0a48d8473ced.pin+0+0000000019.json 719 1697025028000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000020.json 0a48d8473ced.pin+0+0000000020.json 626 1697025031000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000021.json 0a48d8473ced.pin+0+0000000021.json 772 1697025034000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000022.json 0a48d8473ced.pin+0+0000000022.json 582 1697025036000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000023.json 0a48d8473ced.pin+0+0000000023.json 733 1697025037000 dbfs:/mnt/user-0a48d8473ced-bucket/topics/0a48d8473ced.pin/partition=0/0a48d8473ced.pin+0+0000000024.json 0a48d8473ced.pin+0+0000000024.json 727 1697025

In [0]:
#Clean the df_pin DataFrame
#Replace empty entries and entries with no relevant data in each column with Nones
df_pin = df_pin.replace('', None)
df_pin = df_pin.replace(' ', None)
df_pin = df_pin.replace('nan', None)
#Perform the necessary transformations on the follower_count to ensure every entry is a number. 
# Make sure the data type of this column is an int.
#The follower count is a string some with a k or M at the end.
#Replace the k with 000 
#Replace the M with 000000 and convert the string to an integer
df_pin = df_pin.withColumn('follower_count', regexp_replace('follower_count', 'k', '000'))
df_pin = df_pin.withColumn('follower_count', regexp_replace('follower_count', 'M', '000000'))
df_pin = df_pin.withColumn('follower_count', df_pin['follower_count'].cast('int'))
#Clean the data in the save_location column to include only the save location path
#The column contains Local save in /data/path
#Replace Local save in with nothing
df_pin = df_pin.withColumn('save_location', regexp_replace('save_location', 'Local save in ', ''))
#Rename the index column to ind
df_pin = df_pin.withColumnRenamed('index', 'ind')
#Reorder the DataFrame columns to have the following column order:
# ind unique_id title description follower_count poster_name tag_list is_image_or_video
# image_src save_location category
df_pin = df_pin.select('ind', 'unique_id', 'title', 'description', 'follower_count', 'poster_name', 'tag_list', 'is_image_or_video', 'image_src', 'save_location', 'category')

In [0]:
display(df_pin)

ind unique_id title description follower_count poster_name tag_list is_image_or_video image_src save_location category 4387 ae5e7377-f1bd-4ac5-94de-bee317f51a43 Βάπτιση: H παραμυθένια βάπτιση της Τιτίκας με θέμα το μονόκερο από την e.m. for you Το όνομα που επέλεξε η μαμά Ανδριανή για τη γλυκιά Τιτίκα δεν είναι καθόλου τυχαίο. Και φυσικά δεν άφησε τίποτα στην τύχη ούτε την ημέρα της βάπτισης. Ανέθεσε την οργάνωση στην…  4 Manosbojana Katsareas Diy Flowers,Flower Diy,Baptism Decorations,Christening,Event Planning,Wedding Planner,Baptism Ideas,Birthday,Party image https://i.pinimg.com/originals/db/aa/d2/dbaad28fa85012a4ea6958540d98a8e5.jpg /data/event-planning event-planning 6717 bc5ab9ee-505e-44f6-92ba-677fe4fdf3e3 〚 Уютные шведские коттеджи от Carina Olander 〛 ◾ Фото ◾ Идеи ◾ Дизайн Традиционные шведские коттеджи, обычно с красным фасадом — это настоящее воплощением идеального зимнего уюта. Они обычно оформлены очень просто и ✌PUFIK. Beautiful Interiors. On…  136000 PUFIK Interiors & Inspirations Scandinavian Cottage,Swedish Cottage,Swedish Home Decor,Swedish Farmhouse,Swedish Style,Swedish Kitchen,Kitchen Black,Swedish House,Cozy Cottage image https://i.pinimg.com/originals/32/eb/72/32eb72e4fd8654c115a64528bd1f34b4.png /data/home-decor home-decor 4858 58101415-9273-4311-a5bd-0015a56579b4 THE EVENT COLLECTIVE ✖️ on Instagram: “I’ve always loved emerald green 🌲 by @a.purnellproduction Beautiful balloons by @basicallycuteevents @inspiredengravings for the acrylic…” 15.1k Likes, 83 Comments - THE EVENT COLLECTIVE ✖️ (@theeventcollectivex) on Instagram: “I’ve always loved emerald green 🌲 by @a.purnellproduction Beautiful balloons by…” 311 Marie Bradford Diy Birthday Decorations,Balloon Decorations,Table Decorations,Emerald Green Decor,40th Birthday Parties,24th Birthday,Surprise Birthday,Brunch Decor,Quinceanera Themes image https://i.pinimg.com/originals/91/0b/5c/910b5c120f7d1570ffc840302d7b49f4.jpg /data/event-planning event-planning 4608 d234e56f-5b18-4ef3-905b-44103f7719d9 Virtual Baby Shower Little Man Baby Shower Banner, Mustache Baby Shower Backdrop, Oh Boy, Any Color, Printed Or Printable File BBS0035 - 10x8 ft / Top Pole Pocket Wow your guests! Our backdrops are a great option for providing a personalized, stylish and fun addition to your party .It will be the focal point in any event! They are great a…  1000 Iconica Design | Personalized Event Decor, Stationery & Gifts Christmas Party Backdrop,Holiday Banner,Birthday Backdrop,Circus First Birthday,First Birthday Banners,Dinasour Birthday,Birthday Bash,Banner Backdrop,Photo Booth Backdrop image https://i.pinimg.com/originals/15/1f/93/151f93d662dc158ca2c9bbfed198f556.jpg /data/event-planning event-planning 6633 d136f6bc-840d-44f8-bbad-115eb7e6c51e The Cottage Journal on Instagram: “Can you say color?! 😍😍😍 We are loving the cheery vibes that these aqua blue cabinets are giving. If you could paint your cabinets any…” 6,636 Likes, 141 Comments - The Cottage Journal (@thecottagejournal) on Instagram: “Can you say color?! 😍😍😍 We are loving the cheery vibes that these aqua blue cabinets are g…  394 Sarah Martin Diy Kitchen Cabinets,Kitchen Redo,Home Decor Kitchen,New Kitchen,Home Kitchens,Kitchen Remodeling,Aqua Kitchen,Kitchen Counters,Kitchen Islands image https://i.pinimg.com/originals/8c/17/a2/8c17a257b70780480bb89c3699363144.jpg /data/home-decor home-decor 2539 cd2c667e-da47-4818-8f94-3def20b90864 Free Kids Printable - Build a Gingerbread Person Craft - Christmas Activities for Kids | Mrs. Merry Make your own gingerbread person with our free Christmas craft. 4 pages of accessories to mix & match! #gingerbreadchristmasdecor #gingerbreadcraftspreschool #gingerbreadcraftfo…  7000 Mrs. Merry | Free Printables for Kids, Holiday Printables & Party Christmas Projects For Kids,Christmas To Do List,Christmas Decorations For Kids,Christmas Activities For Kids,Preschool Christmas,Free Christmas Printables,Christmas Books,Christmas Themes,Gingerbread Christmas Decor image https://i.pin

In [0]:
#Clean the df_geo dataframe
#Create a new column coordinates that contains an array based on the latitude and longitude columns
df_geo = df_geo.withColumn('coordinates', array('latitude', 'longitude'))
#Drop the latitude and longitude columns from the DataFrame
df_geo = df_geo.drop('latitude', 'longitude')
#Convert the timestamp column from a string to a timestamp data type
df_geo = df_geo.withColumn('timestamp', df_geo['timestamp'].cast('timestamp'))
#Reorder the DataFrame columns to have the following column order:
# ind country coordinates timestamp
df_geo = df_geo.select('ind', 'country', 'coordinates', 'timestamp')

display(df_geo)

ind country coordinates timestamp 9455 British Indian Ocean Territory (Chagos Archipelago) List(-82.9272, -150.346) 2022-03-15T01:46:32.000+0000 6814 British Indian Ocean Territory (Chagos Archipelago) List(-86.5675, -149.565) 2022-09-02T11:34:28.000+0000 7151 British Indian Ocean Territory (Chagos Archipelago) List(-14.6744, -75.3714) 2020-06-05T23:37:24.000+0000 8221 British Indian Ocean Territory (Chagos Archipelago) List(-20.5574, -54.4834) 2021-12-29T06:33:46.000+0000 7569 British Indian Ocean Territory (Chagos Archipelago) List(-86.5675, -149.565) 2018-10-16T08:40:26.000+0000 5111 British Indian Ocean Territory (Chagos Archipelago) List(-83.7472, 8.65953) 2021-04-01T00:56:57.000+0000 2989 British Indian Ocean Territory (Chagos Archipelago) List(-87.013, 133.062) 2020-01-09T19:18:54.000+0000 1624 British Indian Ocean Territory (Chagos Archipelago) List(9.50751, 119.757) 2020-10-24T11:13:47.000+0000 10073 Antarctica (the territory South of 60 deg S) List(-32.8885, -170.295) 2021-06-29T19:56:04.000+0000 10073 Antarctica (the territory South of 60 deg S) List(-32.8885, -170.295) 2021-06-29T19:56:04.000+0000 2418 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2022-05-27T11:30:59.000+0000 2418 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2022-05-27T11:30:59.000+0000 5162 Antarctica (the territory South of 60 deg S) List(-71.6607, -149.206) 2019-09-27T19:06:43.000+0000 1335 Antarctica (the territory South of 60 deg S) List(-77.9931, -175.682) 2022-03-19T17:29:42.000+0000 9185 Antarctica (the territory South of 60 deg S) List(-10.3764, -22.9809) 2019-10-06T18:12:55.000+0000 9335 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2020-11-14T23:42:22.000+0000 6749 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2018-04-16T07:39:46.000+0000 10507 South Georgia and the South Sandwich Islands List(-89.4786, -68.913) 2018-12-27T23:57:31.000+0000 1729 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2021-05-04T14:59:44.000+0000 8836 Antarctica (the territory South of 60 deg S) List(-75.0203, -108.272) 2022-09-06T23:57:01.000+0000 4361 Antarctica (the territory South of 60 deg S) List(-24.8372, -163.337) 2022-07-17T10:48:12.000+0000 9117 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2018-08-02T03:26:24.000+0000 8836 Antarctica (the territory South of 60 deg S) List(-75.0203, -108.272) 2022-09-06T23:57:01.000+0000 5162 Antarctica (the territory South of 60 deg S) List(-71.6607, -149.206) 2019-09-27T19:06:43.000+0000 5625 Antarctica (the territory South of 60 deg S) List(-84.9073, -105.769) 2020-11-22T21:47:04.000+0000 1752 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2020-11-23T15:01:39.000+0000 1872 Antarctica (the territory South of 60 deg S) List(-68.2538, -171.706) 2020-11-02T17:14:08.000+0000 8156 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2022-08-24T22:19:55.000+0000 1910 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2020-06-14T01:25:40.000+0000 9031 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2019-12-15T01:10:49.000+0000 5237 Antarctica (the territory South of 60 deg S) List(-84.9073, -105.769) 2021-07-04T15:50:48.000+0000 2147 Antarctica (the territory South of 60 deg S) List(-88.4642, -171.061) 2018-08-15T14:23:56.000+0000 9121 Antarctica (the territory South of 60 deg S) List(-77.9931, -175.682) 2019-11-03T20:15:30.000+0000 2201 Antarctica (the territory South of 60 deg S) List(-57.9438, -148.044) 2020-02-01T11:55:43.000+0000 5891 Antarctica (the territory South of 60 deg S) List(-68.2538, -171.706) 2021-03-22T00:33:27.000+0000 4739 South Georgia and the South Sandwich Islands List(80.6966, -69.2346) 2020-05-29T08:14:30.000+0000 8577 Antarctica (the territory South of 60 deg S) List(-72.136, -130.529) 2018-05-23T01:53:25.000+0000 5766 South Georgia and the South Sandwich Islands List(-51.534, -82

In [0]:
#Clean the df_user dataframe
#Create a new column user_name that concatenates the information found in the first_name and last_name columns
df_user = df_user.withColumn('user_name', concat(df_user['first_name'], lit(' '), df_user['last_name']))
#Drop the first_name and last_name columns from the DataFrame
df_user = df_user.drop('first_name', 'last_name')
#Convert the date_joined column from a string to a timestamp data type
df_user = df_user.withColumn('date_joined', df_user['date_joined'].cast('timestamp'))
#Reorder the DataFrame columns to have the following column order:
# ind user_name age date_joined
df_user = df_user.select('ind', 'user_name', 'age', 'date_joined')

display(df_user)

ind user_name age date_joined 6353 Christopher Hernandez 42 2017-02-18T00:31:22.000+0000 2015 Christopher Bradshaw 27 2016-03-08T13:38:37.000+0000 10673 Alexander Cervantes 59 2017-05-12T21:22:17.000+0000 1857 Christopher Hamilton 48 2016-02-27T16:57:44.000+0000 10020 Christopher Hawkins 45 2016-09-15T06:02:53.000+0000 2041 Christopher Campbell 35 2015-10-22T22:42:23.000+0000 7031 Christopher Anderson 48 2016-06-13T17:09:14.000+0000 8075 Benjamin Fitzpatrick 50 2017-02-07T08:09:03.000+0000 2539 Christopher Williams 36 2016-06-01T09:41:09.000+0000 6398 Christina Davenport 39 2016-06-29T20:43:59.000+0000 3599 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 4256 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 1901 Michelle Richardson 44 2016-12-18T16:05:39.000+0000 3831 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 6602 Alexandria Anderson 23 2015-10-31T19:20:09.000+0000 4249 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 4245 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 10677 Catherine Mitchell 26 2016-06-16T14:07:36.000+0000 3896 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 2161 Alexander Rodriguez 55 2017-08-12T13:26:38.000+0000 813 Christopher Gonzalez 30 2016-03-02T23:44:12.000+0000 2595 Christopher Barnett 22 2016-03-24T09:38:54.000+0000 3717 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 3475 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 9582 Christopher Hawkins 45 2016-09-15T06:02:53.000+0000 5930 Alexandria Anderson 23 2015-10-31T19:20:09.000+0000 4249 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 3705 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 6156 Christopher Alvarez 28 2016-10-26T19:31:58.000+0000 4245 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 4089 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 4000 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 4222 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 1282 Elizabeth Mccormick 23 2016-10-01T06:22:38.000+0000 4044 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 4008 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 3767 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 4086 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 10190 Jennifer Blanchard 49 2016-05-23T19:42:19.000+0000 4096 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 8221 Christopher Edwards 24 2016-04-06T20:17:29.000+0000 4317 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 3964 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 3539 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 4087 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 3790 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 5076 Christopher Butler 20 2015-12-01T15:08:31.000+0000 7790 Michelle Gutierrez 39 2017-07-19T07:12:04.000+0000 10509 Brittany Thompson 49 2016-04-22T20:36:02.000+0000 10248 Elizabeth English 25 2016-08-19T02:29:26.000+0000 1487 Jonathan Rodriguez 30 2016-09-05T12:31:44.000+0000 10917 Valerie Rodriguez 31 2016-07-30T01:45:47.000+0000 10734 Jennifer Arellano 28 2015-12-18T10:50:10.000+0000 10429 Brandon Henderson 24 2016-01-12T17:59:43.000+0000 2946 Samantha Carpenter 24 2016-06-26T00:05:17.000+0000 10600 Robert Mclaughlin 49 2016-02-27T04:42:03.000+0000 1487 Jonathan Rodriguez 30 2016-09-05T12:31:44.000+0000 4761 Christopher Norman 40 2017-03-07T21:33:30.000+0000 10721 Garrett Hernandez 53 2017-04-05T13:59:02.000+0000 7206 Christina Anderson 27 2016-03-03T11:25:21.000+0000 6806 Christopher Daniel 25 2016-04-15T17:06:49.000+0000 2267 Andrea Blankenship 27 2016-04-11T21:27:52.000+0000 2532 Danielle Hernandez 24 2016-03-24T23:39:08.000+0000 7790 Michelle Gutierrez 39 2017-07-19T07:12:04.000+0000 10675 Christopher Combs 42 2016-02-08T16:47:33.000+0000 1969 Christopher Haynes 25 2016-02-14T23:08:47.000+0000 10274 Kathleen Hamilton 44 2016-12-10T09:13:47.000+0000 9774 Christopher Foster 25 2016-11-01T23:16:19.000+0000 5379 Jonathan Rodriguez 36 2017-08-18T16:25:58.000+0000 2004 Andrea Blankenship 27 2016-04-11T21:27:52.000

In [0]:
#Find the most popular Pinterest category people post to based on their country.
#Your query should return a DataFrame that contains the following columns:
# country category category_count, a new column containing the desired query output

#Create a new DataFrame that contains the country and category columns from the 
# country in df_geo DataFrame 
#and the category column from the df_pin DataFrame
#with the ind column as the join key
df_category_country = df_geo.join(df_pin, df_geo.ind == df_pin.ind).select(df_geo.country, df_pin.category)

df_category_country = df_category_country.groupBy('country', 'category').count()
df_category_country = df_category_country.withColumnRenamed('count', 'category_count')
df_category_country = df_category_country.orderBy('category_count', ascending=False)
df_category_country = df_category_country.dropDuplicates(['country'])
df_category_country = df_category_country.select('country', 'category', 'category_count')

display(df_category_country)


country category category_count Afghanistan education 29 Albania art 40 Algeria quotes 53 American Samoa tattoos 18 Andorra tattoos 11 Angola diy-and-crafts 7 Anguilla diy-and-crafts 9 Antarctica (the territory South of 60 deg S) christmas 11 Antigua and Barbuda travel 8 Argentina tattoos 22 Armenia diy-and-crafts 26 Aruba tattoos 25 Australia christmas 7 Austria travel 9 Azerbaijan finance 12 Bahamas art 16 Bahrain finance 7 Bangladesh christmas 14 Barbados travel 10 Belarus christmas 2 Belgium diy-and-crafts 5 Belize diy-and-crafts 11 Benin finance 3 Bermuda christmas 12 Bhutan event-planning 6 Bolivia diy-and-crafts 9 Bosnia and Herzegovina art 4 Botswana tattoos 17 Bouvet Island (Bouvetoya) event-planning 7 Brazil finance 3 British Indian Ocean Territory (Chagos Archipelago) mens-fashion 3 British Virgin Islands event-planning 9 Brunei Darussalam event-planning 3 Bulgaria christmas 14 Burkina Faso quotes 10 Burundi mens-fashion 5 Cambodia vehicles 9 Cameroon art 5 Canada travel 2 Cape Verde education 9 Cayman Islands travel 1 Central African Republic education 4 Chad diy-and-crafts 5 Chile travel 2 China finance 1 Christmas Island travel 5 Cocos (Keeling) Islands vehicles 4 Colombia finance 14 Comoros quotes 2 Congo art 6 Cook Islands diy-and-crafts 1 Costa Rica christmas 5 Cote d'Ivoire travel 5 Croatia finance 4 Cuba diy-and-crafts 3 Cyprus quotes 4 Czech Republic travel 3 Denmark beauty 4 Djibouti diy-and-crafts 3 Dominica christmas 2 Dominican Republic home-decor 10 Ecuador travel 4 Egypt mens-fashion 9 El Salvador beauty 1 Equatorial Guinea event-planning 1 Eritrea art 1 Estonia vehicles 2 Ethiopia home-decor 4 Falkland Islands (Malvinas) event-planning 5 Faroe Islands event-planning 10 Fiji mens-fashion 2 Finland finance 5 France diy-and-crafts 2 French Guiana quotes 9 French Polynesia diy-and-crafts 9 French Southern Territories finance 4 Gabon travel 3 Gambia art 1 Georgia education 11 Germany event-planning 2 Ghana art 5 Gibraltar travel 2 Greece mens-fashion 6 Greenland education 1 Grenada vehicles 4 Guadeloupe christmas 6 Guam mens-fashion 1 Guatemala art 2 Guernsey tattoos 2 Guinea finance 4 Guinea-Bissau vehicles 4 Guyana tattoos 1 Haiti christmas 1 Heard Island and McDonald Islands mens-fashion 2 Holy See (Vatican City State) event-planning 1 Honduras event-planning 2 Hong Kong home-decor 2 Hungary vehicles 3 Iceland diy-and-crafts 1 India finance 4 Indonesia finance 8 Iran art 2 Iraq tattoos 2 Ireland event-planning 4 Isle of Man art 3 Israel finance 4 Italy beauty 1 Jamaica education 4 Japan art 2 Jersey mens-fashion 1 Jordan beauty 1 Kazakhstan christmas 4 Kenya diy-and-crafts 5 Kiribati beauty 5 Korea travel 5 Kuwait christmas 2 Kyrgyz Republic christmas 1 Lao People's Democratic Republic beauty 1 Latvia mens-fashion 4 Lebanon mens-fashion 4 Lesotho art 14 Liberia event-planning 1 Libyan Arab Jamahiriya christmas 2 Liechtenstein quotes 4 Lithuania education 4 Luxembourg education 2 Macao vehicles 4 Macedonia finance 1 Madagascar mens-fashion 1 Malawi travel 2 Maldives beauty 4 Mali christmas 1 Malta art 4 Marshall Islands vehicles 1 Martinique christmas 1 Mauritania travel 1 Mauritius quotes 1 Mayotte diy-and-crafts 4 Mexico home-decor 2 Micronesia travel 1 Moldova beauty 2 Monaco vehicles 4 Mongolia mens-fashion 4 Montenegro finance 1 Montserrat vehicles 2 Morocco quotes 10 Mozambique home-decor 13 Myanmar christmas 2 Namibia quotes 4 Nauru beauty 6 Nepal christmas 1 Netherlands home-decor 6 Netherlands Antilles beauty 5 New Caledonia travel 2 New Zealand quotes 2 Nicaragua mens-fashion 2 Niger christmas 2 Nigeria education 5 Niue quotes 2 Norfolk Island mens-fashion 5 Norway art 4 Oman finance 1 Pakistan christmas 4 Palau vehicles 1 Palestinian Territory vehicles 4 Panama travel 4 Papua New Guinea quotes 6 Paraguay vehicles 1 Peru art 4 Philippines vehicles 1 Pitcairn Islands diy-and-crafts 2 Poland diy-and-crafts 1 Portugal diy-and-crafts 1 Puerto Rico christmas 2 Qatar beauty 2 Reunion home-decor 1 Ro

In [0]:
#Find how many posts each category had between 2018 and 2022.

#Return a DataFrame that contains the following columns:
# post_year, a new column that contains only the year from the timestamp column in df_geo
# category from the df_pin DataFrame
# category_count, a new column containing the desired query output

#join the two DataFrames on the ind column and select the post_year using the year from the timestamp and category columns
df_category_year = df_geo.join(df_pin, df_geo.ind == df_pin.ind).select(year(df_geo.timestamp).alias('post_year'), df_pin.category)
df_category_year = df_category_year.groupBy('post_year', 'category').count()
df_category_year = df_category_year.withColumnRenamed('count', 'category_count')
df_category_year = df_category_year.orderBy('post_year', ascending=False)
df_category_year = df_category_year.select('post_year', 'category', 'category_count')
df_category_year = df_category_year.filter(df_category_year.post_year >= 2018)
df_category_year = df_category_year.filter(df_category_year.post_year <= 2022)
display(df_category_year)

post_year category category_count 2022 vehicles 27 2022 travel 38 2022 beauty 41 2022 finance 43 2022 event-planning 28 2022 tattoos 39 2022 mens-fashion 24 2022 christmas 58 2022 art 41 2022 diy-and-crafts 34 2022 home-decor 26 2022 education 31 2022 quotes 50 2021 mens-fashion 47 2021 event-planning 43 2021 diy-and-crafts 46 2021 travel 39 2021 art 55 2021 finance 60 2021 tattoos 47 2021 education 56 2021 beauty 27 2021 quotes 55 2021 vehicles 44 2021 christmas 45 2021 home-decor 29 2020 quotes 38 2020 finance 51 2020 tattoos 36 2020 mens-fashion 79 2020 vehicles 28 2020 event-planning 41 2020 art 57 2020 travel 46 2020 beauty 42 2020 diy-and-crafts 55 2020 christmas 45 2020 home-decor 45 2020 education 44 2019 art 49 2019 education 43 2019 event-planning 32 2019 mens-fashion 31 2019 home-decor 40 2019 christmas 45 2019 finance 28 2019 travel 50 2019 quotes 42 2019 vehicles 38 2019 diy-and-crafts 41 2019 tattoos 41 2019 beauty 22 2018 christmas 50 2018 beauty 34 2018 tattoos 36 2018 finance 34 2018 home-decor 31 2018 diy-and-crafts 60 2018 vehicles 36 2018 education 47 2018 event-planning 37 2018 travel 56 2018 art 48 2018 quotes 46 2018 mens-fashion 41

In [0]:
#Find the user with the most followers in each country.
#For each country find the user with the most followers.
#Your query should return a DataFrame that contains the following columns:
#country poster_name follower_count

#country is from df_geo
#poster_name and follower_count are from df_pin
#join the two DataFrames on the ind column and select the country, poster_name, and follower_count columns
df_most_followers_per_country = df_geo.join(df_pin, df_geo.ind == df_pin.ind).select(df_geo.country, df_pin.poster_name, df_pin.follower_count)
df_most_followers_per_country = df_most_followers_per_country.groupBy('country', 'poster_name').max('follower_count')
df_most_followers_per_country = df_most_followers_per_country.withColumnRenamed('max(follower_count)', 'follower_count')
df_most_followers_per_country = df_most_followers_per_country.orderBy('follower_count', ascending=False)
df_most_followers_per_country = df_most_followers_per_country.dropDuplicates(['country'])
df_most_followers_per_country = df_most_followers_per_country.select('country', 'poster_name', 'follower_count')
display(df_most_followers_per_country)

country poster_name follower_count Afghanistan 9GAG 3000000 Albania The Minds Journal 5000000 Algeria Apartment Therapy 5000000 American Samoa Mamas Uncut 8000000 Andorra Teachers Pay Teachers 1000000 Angola Tastemade 8000000 Anguilla We Heart It 15000000 Antarctica (the territory South of 60 deg S) Refinery29 1000000 Antigua and Barbuda Country Living Magazine 1000000 Argentina Cheezburger 2000000 Armenia Michelle {CraftyMorning.com} 892000 Aruba GQ Magazine 874000 Australia Mujer de 10 2000000 Austria Allwomenstalk - girl rules 813000 Azerbaijan Style Me Pretty 6000000 Bahamas Handmade Charlotte 948000 Bahrain Rainy Day Mum 337000 Bangladesh Better Homes and Gardens 4000000 Barbados The Creativity Exchange 410000 Belarus Prudent Penny Pincher - Home Decor, Organization, Crafts, Recipes 648000 Belgium This Old House 944000 Belize Easy Kids Crafts & Activities | Preschool & Kindergarten Ideas 267000 Benin Decoist.com 432000 Bermuda 3 Boys and a Dog 83000 Bhutan Esquire Magazine 130000 Bolivia The Kitchn 1000000 Bosnia and Herzegovina Stylesatlife 388000 Botswana OkChicas 3000000 Bouvet Island (Bouvetoya) POPSUGAR 5000000 Brazil Doris Leslie Blau Antique & Vintage Rugs 72000 British Indian Ocean Territory (Chagos Archipelago) Design Rulz 248000 British Virgin Islands The WHOot 1000000 Brunei Darussalam Kids Craft Room 277000 Bulgaria Half Baked Harvest 912000 Burkina Faso Behance 6000000 Burundi Macho Moda 620000 Cambodia Catch My Party 2000000 Cameroon The Blonde Abroad 123000 Canada Giorgenti New York 258000 Cape Verde Sand and Sisal 178000 Cayman Islands InStyle 1000000 Central African Republic PureWow 868000 Chad Glued To My Crafts 226000 Chile Local Adventurer - Las Vegas + Worldwide Travel Blog 89000 China Empowered Sustenance 127000 Christmas Island Instructables 3000000 Cocos (Keeling) Islands How Does She 709000 Colombia DIY Magazine 466000 Comoros Ruffled 4000000 Congo Virginia | Fynes Designs : Home Decor, Easy DIY’s, Lifestyle 410000 Cook Islands Fun Loving Families: Crafts, Games, and Activities for Kids 31000 Costa Rica Martha Stewart Living 2000000 Cote d'Ivoire Mom Junction 565000 Croatia Glowsly 157000 Cuba Cuded Art & Design 1000000 Cyprus Porchdotcom 117000 Czech Republic Tatertots and Jello .com 398000 Denmark A Life Adjacent 36000 Djibouti El Hombre 307000 Dominica Monique - Living Life and Learning 67000 Dominican Republic My Modern Met 3000000 Ecuador LABONNI 84000 Egypt Allure 346000 El Salvador Power of Positivity 221000 Equatorial Guinea Whisper Wanderlust * Travel Blog 10000 Eritrea Core77 105000 Estonia Morgan | Modernly Morgan 13000 Ethiopia Refresh Restyle Debbie DIY Home Decor, Chalk Couture Designer 253000 Falkland Islands (Malvinas) A Blissful Nest 113000 Faroe Islands Veterans United Home Loans 11000 Fiji Teach Create Motivate 41000 Finland Buggy and Buddy 185000 France Hello Lovely 115000 French Guiana Sweet Red Poppy Free Sewing Patterns, Cut Files & Craft Tutorials 241000 French Polynesia Hunker 279000 French Southern Territories Don't Waste the Crumbs 119000 Gabon Angela Watson's Truth for Teachers 88000 Gambia The Travel Hacking Life 61000 Georgia Susie Allison | Busy Toddler 203000 Germany Michael Friermood 48000 Ghana Zina Harrington 1000000 Gibraltar TheSuperBOO! 89000 Greece Thirty Handmade Days 397000 Greenland The Educators' Spin On It 2000000 Grenada The Mighty 185000 Guadeloupe Kathy+Steve | TBD + TGG + OhMeOhMy 355000 Guam imgur 4000000 Guatemala Homedit.com 965000 Guernsey SuzysSitcom 58000 Guinea Cars Zone 134000 Guinea-Bissau Kristina Buskirk | Toddler Approved 160000 Guyana J ♥ Millennial Boss 29000 Haiti Fres Houz 100000 Heard Island and McDonald Islands Real Men Real Style 487000 Holy See (Vatican City State) Viva Decora 2000000 Honduras Mad in Crafts 106000 Hong Kong Remodelista 991000 Hungary Weed 'em & Reap 77000 Iceland The Hundreds 5000 India Happiness is Homemade | Crafts, Printables, Party Ideas, & More! 167000 Indonesia Forbes 252000 Iran WeddingWire 520000 Iraq Hous

In [0]:
#Find the country with the user with most followers.
#Return a DataFrame (with one entry) that contains the following columns:
#country follower_count

df_most_followed = df_most_followers_per_country.groupBy('country').max('follower_count')
df_most_followed = df_most_followed.withColumnRenamed('max(follower_count)', 'follower_count')
df_most_followed = df_most_followed.orderBy('follower_count', ascending=False)

#limit to one entry
df_most_followed = df_most_followed.limit(1)
display(df_most_followed)

country follower_count Anguilla 15000000

In [0]:
#Find the most popular category for different age groups.

#The query returns a DataFrame that contains the following columns:
#age_group, a new column based on the original age column in df_user
#category from df_pin
#category_count, a new column containing the desired query output

#The following age groups are used:
# 18-24 25-35 36-50 50+

#Join DataFrames using ind column
df_age_groups_category = df_pin.join(df_user, df_pin.ind == df_user.ind).select(df_user.age, df_pin.category)
#Create a new column age_group that contains the age group based on the age column
df_age_groups_category = df_age_groups_category.withColumn('age_group', when((df_age_groups_category.age >= 18) & (df_age_groups_category.age <= 24), '18-24')
                                                           .when((df_age_groups_category.age >= 25) & (df_age_groups_category.age <= 35), '25-35')
                                                           .when((df_age_groups_category.age >= 36) & (df_age_groups_category.age <= 50), '36-50')
                                                           .when(df_age_groups_category.age > 50, '50+')
                                                           .otherwise('Unknown'))
df_age_groups_category = df_age_groups_category.groupBy('age_group', 'category').count()
df_age_groups_category = df_age_groups_category.withColumnRenamed('count', 'category_count')
df_age_groups_category = df_age_groups_category.orderBy('age_group', ascending=True)
df_age_groups_category = df_age_groups_category.select('age_group', 'category', 'category_count')
display(df_age_groups_category)


age_group category category_count 50+ travel 15 50+ event-planning 22 50+ christmas 17 50+ tattoos 5 50+ diy-and-crafts 9 50+ quotes 14 50+ beauty 26 50+ finance 9 50+ mens-fashion 22 50+ education 12 50+ vehicles 29 50+ home-decor 12 50+ art 14 36-50 christmas 46 36-50 travel 57 36-50 finance 71 36-50 vehicles 45 36-50 mens-fashion 35 36-50 tattoos 28 36-50 home-decor 42 36-50 education 34 36-50 diy-and-crafts 30 36-50 event-planning 44 36-50 quotes 54 36-50 art 50 36-50 beauty 39 25-35 travel 87 25-35 mens-fashion 54 25-35 christmas 81 25-35 beauty 50 25-35 tattoos 22 25-35 education 72 25-35 quotes 47 25-35 finance 62 25-35 event-planning 70 25-35 home-decor 56 25-35 vehicles 68 25-35 diy-and-crafts 79 25-35 art 54 18-24 education 109 18-24 diy-and-crafts 120 18-24 finance 76 18-24 event-planning 55 18-24 quotes 124 18-24 christmas 112 18-24 home-decor 67 18-24 beauty 52 18-24 vehicles 43 18-24 art 142 18-24 tattoos 148 18-24 mens-fashion 119 18-24 travel 74

In [0]:
#Find the median follower count for these age groups:
#18-24 25-35 36-50 50+

#This query returns a DataFrame that contains the following columns:
#age_group, a new column based on the original age column from df_user
#median_follower_count, a new column containing the desired query output, follower_count is from df_pin

df_median_followers = df_pin.join(df_user, df_pin.ind == df_user.ind).select(df_user.age, df_pin.follower_count)
df_median_followers = df_median_followers.withColumn('age_group', when((df_median_followers.age >= 18) & (df_median_followers.age <= 24), '18-24')
							     .when((df_median_followers.age >= 25) & (df_median_followers.age <= 35), '25-35')
							     .when((df_median_followers.age >= 36) & (df_median_followers.age <= 50), '36-50')
							     .when(df_median_followers.age > 50, '50+')	
							     .otherwise('Unknown'))

#calculate median follower count
df_median_followers = df_median_followers.groupBy('age_group').agg(expr('percentile(follower_count, 0.5)').alias('median_follower_count'))
df_median_followers = df_median_followers.orderBy('age_group', ascending=True)
display(df_median_followers)

age_group median_follower_count 18-24 130000.0 25-35 26000.0 36-50 7000.0 50+ 877.0

In [0]:
#Find how many users have joined each year.

#This query returns a DataFrame that contains the following columns:
#post_year, a new column that contains only the year from the timestamp column in df_user
#number_users_joined, a new column containing the desired query output

df_users_joined = df_user.select(year(df_user.date_joined).alias('post_year'))
df_users_joined = df_users_joined.groupBy('post_year').count()
df_users_joined = df_users_joined.withColumnRenamed('count', 'number_users_joined')
df_users_joined = df_users_joined.orderBy('post_year', ascending=True)
display(df_users_joined)

post_year number_users_joined 2015 894 2016 1004 2017 359

In [0]:
#Find median follower count of users based on the year they joined.

#For years joined between 2015 and 2020.
#This query should return a DataFrame that contains the following columns:
#post_year, a new column that contains only the year from the timestamp column
#median_follower_count, a new column containing the desired query output

df_users_joined_median_follower_count = df_user.join(df_pin, df_user.ind == df_pin.ind).select(year(df_user.date_joined).alias('post_year'), df_pin.follower_count)
df_users_joined_median_follower_count = df_users_joined_median_follower_count.groupBy('post_year').agg(expr('percentile(follower_count, 0.5)').alias('median_follower_count'))
df_users_joined_median_follower_count = df_users_joined_median_follower_count.orderBy('post_year', ascending=True)
df_users_joined_median_follower_count = df_users_joined_median_follower_count.filter(df_users_joined_median_follower_count.post_year >= 2015)
df_users_joined_median_follower_count = df_users_joined_median_follower_count.filter(df_users_joined_median_follower_count.post_year <= 2020)
display(df_users_joined_median_follower_count)


post_year median_follower_count 2015 163000.0 2016 18000.0 2017 4000.0

In [0]:
#Find the median follower count of users that have joined between 2015 and 2020, based on which age group they are part of.

#This query should return a DataFrame that contains the following columns:
#age_group, a new column based on the original age column from df_user
#post_year, a new column that contains only the year from the timestamp column from df_user
#median_follower_count, a new column containing the desired query output, from df_pin

df_med_followers_for_year_age_group = df_user.join(df_pin, df_user.ind == df_pin.ind).select(df_user.age, year(df_user.date_joined).alias('post_year'), df_pin.follower_count)
df_med_followers_for_year_age_group = df_med_followers_for_year_age_group.withColumn('age_group', when((df_med_followers_for_year_age_group.age >= 18) & (df_med_followers_for_year_age_group.age <= 24), '18-24')
														 .when((df_med_followers_for_year_age_group.age >= 25) & (df_med_followers_for_year_age_group.age <= 35), '25-35')
														 .when((df_med_followers_for_year_age_group.age >= 36) & (df_med_followers_for_year_age_group.age <= 50), '36-50')
														 .when(df_med_followers_for_year_age_group.age > 50, '50+')
														 .otherwise('Unknown'))
df_med_followers_for_year_age_group = df_med_followers_for_year_age_group.groupBy('post_year', 'age_group').agg(expr('percentile(follower_count, 0.5)').alias('median_follower_count'))
df_med_followers_for_year_age_group = df_med_followers_for_year_age_group.orderBy('post_year', ascending=True)
df_med_followers_for_year_age_group = df_med_followers_for_year_age_group.filter(df_med_followers_for_year_age_group.post_year >= 2015)
df_med_followers_for_year_age_group = df_med_followers_for_year_age_group.filter(df_med_followers_for_year_age_group.post_year <= 2020)
display(df_med_followers_for_year_age_group)

post_year age_group median_follower_count 2015 50+ 14000.0 2015 25-35 44000.0 2015 18-24 228000.0 2015 36-50 11000.0 2016 36-50 9500.0 2016 25-35 24000.0 2016 50+ 457.0 2016 18-24 37000.0 2017 36-50 3000.0 2017 25-35 6000.0 2017 18-24 4000.0 2017 50+ 2000.0